# Feature Engineering

## Time and Lag Features

In [3]:
import matplotlib.pyplot as plt
import seaborn as sns
import pandas as pd
import numpy as np
from darts import TimeSeries
file_path = "./data/weatherkit_plus_load.csv"  # Update with actual path
df = pd.read_csv(file_path, parse_dates=['event_timestamp'])

df['event_timestamp'] = pd.to_datetime(df['event_timestamp'])
df = df.set_index('event_timestamp').sort_index()

# Extract time-based features
df['hour'] = df.index.hour
df['minute'] = df.index.minute
df['day_of_week'] = df.index.dayofweek
df['is_weekend'] = df['day_of_week'] >= 5
df['month'] = df.index.month
df['time_step'] = df['hour'] * 4 + df['minute'] // 15
df['hour_sin'] = np.sin(2 * np.pi * df['hour'] / 24)
df['hour_cos'] = np.cos(2 * np.pi * df['hour'] / 24)
df['step_sin'] = np.sin(2 * np.pi * df['time_step'] / 96)
df['step_cos'] = np.cos(2 * np.pi * df['time_step'] / 96)
df['is_peak_time'] = df['time_step'].between(40, 64)
df['is_morning_surge'] = df['time_step'].between(26, 38)

# # Compute lag features
df['lag_1'] = df['load_MW'].shift(1)
df['lag_4'] = df['load_MW'].shift(4)
df['lag_96'] = df['load_MW'].shift(96)
df['lag_672'] = df['load_MW'].shift(672)

# Rolling statistics
df['rolling_mean_4'] = df['load_MW'].rolling(window=4).mean()
# df['rolling_std_4'] = df['load_MW'].rolling(window=4).std()
df['rolling_mean_96'] = df['load_MW'].rolling(window=96).mean()
# df['rolling_std_96'] = df['load_MW'].rolling(window=96).std()
df['rolling_mean_672'] = df['load_MW'].rolling(window=672).mean()
# df['rolling_std_672'] = df['load_MW'].rolling(window=672).std()

# # Historical average from same time 30 days ago (2880 = 96 * 30)
# df['avg_same_slot_30_days_ago'] = df['load_MW'].shift(2880)

# Define observed and forecasted feature sets
observed_features = [
    'weatherkit_observed_temperature_C',
    'weatherkit_observed_humidity_pc',
    'weatherkit_observed_air_pressure_kPa',
    'weatherkit_observed_cloud_cover_pc',
    'weatherkit_observed_wind_speed_km_h'
]

observed_wind_dir = 'weatherkit_observed_wind_direction_deg'

forecasted_features = [
    'weatherkit_forecast_temp_C',
    'weatherkit_forecast_humidity_pc',
    'weatherkit_forecast_air_pressure_kPa',
    'weatherkit_forecast_cloud_cover_pc',
    'weatherkit_forecast_wind_speed_km_h'
]

forecasted_wind_dir = 'weatherkit_forecast_wind_direction_deg'

# Add lag/rolling features for observed weather (excluding wind direction)
for feature in observed_features:
    df[f'{feature}_lag_1'] = df[feature].shift(1)
    df[f'{feature}_lag_4'] = df[feature].shift(4)
    df[f'{feature}_lag_96'] = df[feature].shift(96)
    df[f'{feature}_rolling_mean_4'] = df[feature].rolling(window=4).mean()
    df[f'{feature}_rolling_mean_96'] = df[feature].rolling(window=96).mean()
    df[f'{feature}_rolling_mean_672'] = df[feature].rolling(window=672).mean()

# Add cyclical transforms for wind direction only
df['observed_wind_dir_sin'] = np.sin(np.radians(df[observed_wind_dir]))
df['observed_wind_dir_cos'] = np.cos(np.radians(df[observed_wind_dir]))
df['forecasted_wind_dir_sin'] = np.sin(np.radians(df[forecasted_wind_dir].shift(-96)))
df['forecasted_wind_dir_cos'] = np.cos(np.radians(df[forecasted_wind_dir].shift(-96)))

# Forecasted features: lag_96 simulating known forecast at time t for t+96
for feature in forecasted_features:
    df[f'{feature}_lag_96'] = df[feature].shift(-96)

# 1. Basic time and load features
core_features = [
    'hour', 'day_of_week', 'is_weekend', 'month', 'time_step',
    'hour_sin', 'hour_cos',
    'is_peak_time', 'is_morning_surge',
    'lag_1', 'lag_4', 'lag_96', 'lag_672',
    'rolling_mean_4', 'rolling_mean_96', 'rolling_mean_672',
    'observed_wind_dir_sin', 'observed_wind_dir_cos',
    'forecasted_wind_dir_sin', 'forecasted_wind_dir_cos',
]

# 2. Observed weather lags & rolling
observed_lag_roll = [
    f'weatherkit_observed_{w}_{suffix}'
    for w in ['temperature_C', 'humidity_pc', 'air_pressure_kPa', 'cloud_cover_pc', 'wind_speed_km_h']
    for suffix in ['lag_1', 'lag_4', 'lag_96', 'rolling_mean_4', 'rolling_mean_96', 'rolling_mean_672']
]

# 3. Forecasted weather (lag_96)
forecasted_lag_96 = [
    f'weatherkit_forecast_{w}_lag_96'
    for w in ['temp_C', 'humidity_pc', 'air_pressure_kPa', 'cloud_cover_pc', 'wind_speed_km_h']
]


# Combine all
selected_features = core_features + observed_lag_roll + forecasted_lag_96

# Filter DataFrame
df_selected = df[selected_features].dropna()

# Recreate timestamps and y_df
timestamps = df_selected.index[96:-96]
X_df_filtered = df_selected.loc[timestamps].reset_index()
X_df_filtered.rename(columns={"event_timestamp": "timestamp"}, inplace=True)

y = []
for t in range(96, len(df_selected) - 96):
    y.append(df['load_MW'].iloc[t + 1:t + 97].values)

y_df_filtered = pd.DataFrame(y, columns=[f'load_t+{i+1}' for i in range(96)])
y_df_filtered['timestamp'] = timestamps

pd.set_option('future.no_silent_downcasting', True)
# Step 1: Strip timezone info
X_df_filtered['timestamp'] = pd.to_datetime(X_df_filtered['timestamp']).dt.tz_localize(None)
y_df_filtered['timestamp'] = pd.to_datetime(y_df_filtered['timestamp']).dt.tz_localize(None)

# Step 2: Create full time range and reindex to fill any gaps
full_index = pd.date_range(
    start=X_df_filtered['timestamp'].min(),
    end=X_df_filtered['timestamp'].max(),
    freq='15min'
)

X_df_filtered = X_df_filtered.set_index('timestamp').reindex(full_index).ffill().reset_index().rename(columns={'index': 'timestamp'})
y_df_filtered = y_df_filtered.set_index('timestamp').reindex(full_index).ffill().reset_index().rename(columns={'index': 'timestamp'})

# Step 3: Convert to Darts TimeSeries with proper freq
target_series = TimeSeries.from_dataframe(
    y_df_filtered,
    time_col='timestamp',
    value_cols=[f'load_t+{i+1}' for i in range(96)],
    fill_missing_dates=True,
    freq="15min"
)

covariate_series = TimeSeries.from_dataframe(
    X_df_filtered,
    time_col='timestamp',
    value_cols=[col for col in X_df_filtered.columns if col != 'timestamp'],
    fill_missing_dates=True,
    freq="15min"
)


# Observed and forecasted Features

In [12]:
from darts.models import LightGBMModel

# Define the model
model = LightGBMModel(
    lags=None,  # no lags on target since it's exogenous
    lags_past_covariates=[-1],
    lags_future_covariates=[0],
    # lags_past_covariates=[-1, -4, -96, -672],
    # lags_future_covariates=[0],
    output_chunk_length=96,
    multi_models=True,           #
    random_state=42,
    n_jobs=-1,
    verbose=1
)
model.fit(
    series=target_series,
    past_covariates=covariate_series,
    future_covariates=covariate_series,
    # verbose=True
)

[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.003012 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 21582
[LightGBM] [Info] Number of data points in the train set: 11096, number of used features: 116
[LightGBM] [Info] Start training from score 364.888324
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.007720 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 21582
[LightGBM] [Info] Number of data points in the train set: 11096, number of used features: 116
[LightGBM] [Info] Start training from score 364.917759
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.010742 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] 

LightGBMModel(lags=None, lags_past_covariates=[-1], lags_future_covariates=[0], output_chunk_length=96, output_chunk_shift=0, add_encoders=None, likelihood=None, quantiles=None, random_state=42, multi_models=True, use_static_covariates=True, categorical_past_covariates=None, categorical_future_covariates=None, categorical_static_covariates=None, n_jobs=-1, verbose=1)

In [16]:
model.save("./models/lightgbm_model.pkl")


In [12]:
from darts.models import LightGBMModel

model = LightGBMModel.load("./models/lightgbm_model.pkl")
from darts.metrics import mape, smape, mae

# Generate historical forecasts
forecast = model.historical_forecasts(
    series=target_series,
    past_covariates=covariate_series,
    future_covariates=covariate_series,
    start=0.7,  # start backtest at 80% of the series length
    forecast_horizon=96,
    stride=96,  # step forward 96 timesteps each time
    retrain=False,  # if True, retrain model at each step
    verbose=True,
    last_points_only=False  # <<< KEY to getting full forecast windows

)


historical forecasts:   0%|          | 0/1 [00:00<?, ?it/s]

/Users/sham/PycharmProjects/LoadPrediction/.venv/lib/python3.10/site-packages/sklearn/utils/validation.py:2739: UserWarning: X does not have valid feature names, but LGBMRegressor was fitted with feature names
  warnings.warn(
/Users/sham/PycharmProjects/LoadPrediction/.venv/lib/python3.10/site-packages/sklearn/utils/validation.py:2739: UserWarning: X does not have valid feature names, but LGBMRegressor was fitted with feature names
  warnings.warn(
/Users/sham/PycharmProjects/LoadPrediction/.venv/lib/python3.10/site-packages/sklearn/utils/validation.py:2739: UserWarning: X does not have valid feature names, but LGBMRegressor was fitted with feature names
  warnings.warn(
/Users/sham/PycharmProjects/LoadPrediction/.venv/lib/python3.10/site-packages/sklearn/utils/validation.py:2739: UserWarning: X does not have valid feature names, but LGBMRegressor was fitted with feature names
  warnings.warn(
/Users/sham/PycharmProjects/LoadPrediction/.venv/lib/python3.10/site-packages/sklearn/utils/

In [24]:
from darts.metrics import mape, smape, mae

actual_series_list = [
    target_series.slice(f.start_time(), f.end_time()) for f in forecast
]

print("MAPE:", mape(actual_series_list, forecast))
print("sMAPE:", smape(actual_series_list, forecast))
print("MAE:", mae(actual_series_list, forecast))

MAPE: [1.4473514723878107, 1.6756031975552244, 1.773259023406278, 1.4290516213066724, 1.729656206188423, 1.6331715113144363, 1.1598850480104734, 1.2396930674764393, 1.1872312027527527, 1.7220690594168049, 1.5556410139838117, 1.5017732579575875, 1.3386851825994193, 1.1646643142176127, 1.159453817114682, 1.3381964242628797, 1.4617894654910295, 1.4160315007104856, 1.113288843889311, 1.1440996489039383, 1.627896753772425, 1.6338430701025628, 1.7270976091670551, 1.7183045836027304, 1.4293859021503954, 1.3497410353816928, 1.4011971309919076, 1.338054664987099, 1.550333021710873, 1.332467883166943, 1.5041322849341918, 1.431476100749651, 1.7425330845783407, 3.6448443667917503]
sMAPE: [1.4393766483055355, 1.6754524314009356, 1.7661266056868037, 1.437121995410858, 1.7179309178169107, 1.6480619949412578, 1.1602854858079061, 1.2394460957528173, 1.1837229541771646, 1.705316980668229, 1.5544714235173067, 1.5048808309750639, 1.3354553760118149, 1.1635269971070685, 1.163660155014252, 1.341869514915876

In [13]:
import matplotlib.pyplot as plt

# Get the first forecasted series
single_forecast = forecast[0]

# Get the corresponding actual values for the same time window
actual_window = target_series.slice_intersect(single_forecast)

# Plot
plt.figure(figsize=(12, 4))
single_forecast.plot(label="Forecast")
actual_window.plot(label="Actual")
plt.title("Forecast vs Actual - Single Window")
plt.legend()
plt.grid(True)
plt.show()

Number of series components (96) is larger than the maximum number of components to plot (10). Plotting only the first `10` components. You can adjust the number of components to plot using `max_nr_components`.
Number of series components (96) is larger than the maximum number of components to plot (10). Plotting only the first `10` components. You can adjust the number of components to plot using `max_nr_components`.


In [15]:
import matplotlib.pyplot as plt

# Extract only t+1 prediction (first column)
forecast_t1 = single_forecast[:, 0]  # or single_forecast.univariate_component(0)
actual_t1 = actual_window[:, 0]

# Plot only t+1
plt.figure(figsize=(12, 4))
forecast_t1.plot(label="Forecast t+1")
actual_t1.plot(label="Actual t+1")
plt.title("Forecast vs Actual - t+1 Only")
plt.legend()
plt.grid(True)
plt.show()


# Assemble X_t and Y_t

# Train LightGBM Model